In [1]:
import h5py
import numpy as np
import matplotlib.pyplot as plt
import scipy.signal as signal
import glob

In [2]:
data_path = 'C:\\Users\\SogaSensingGroup\\Desktop\\seis'

In [3]:
chan_range  = [1200, 1400]

In [4]:
row1 = 0
count = 0

for h5name in glob.glob(data_path + '\\campus_fiber*.h5'):
    count += 1
    f = h5py.File(h5name, 'r')
    RawData = f['Acquisition']['Raw[0]']['RawData']
    
    RawDataTime = f['Acquisition']['Raw[0]']['RawDataTime']
    if row1 == 0:
        all_RawData = np.array(RawData[:, chan_range[0]:chan_range[1]])
        all_RawDataTime = np.array(RawDataTime)
        row1 = all_RawData.shape[0]

    else:
        all_RawData = np.append(all_RawData,RawData[:, chan_range[0]:chan_range[1]],axis=0)
        all_RawDataTime = np.append(all_RawDataTime,RawDataTime,axis=0)
        row1 = all_RawData.shape[0]

        
all_RawData = np.transpose(all_RawData)

channels = all_RawData.shape[0]
total_time = (all_RawDataTime[-1] - all_RawDataTime[0])/10**6

print(str(count)+' files imported. There are '+ str(total_time) +
      ' seconds recorded on '+
      str(channels) + ' channels...')

20 files imported. There are 299.9996 seconds recorded on 200 channels...


In [5]:
fs = 1/(all_RawDataTime[1]-all_RawDataTime[0])*10**6
print(fs)

2500.0


In [6]:
t = (all_RawDataTime - all_RawDataTime[0])/10**6

In [7]:
sos = signal.butter(3, [5,20], 'bp', fs=fs, output='sos')
all_ProcData = np.zeros(all_RawData.shape)

for i in range(all_RawData.shape[0]):
    data = all_RawData[i, :] 
    sig_phi = data*pi/2**15 #radians
    sig_ep2 = 1550*sig_phi/(4*pi*1.465*2.041905*10**9*0.78)*10**9
    sig_fil = signal.sosfilt(sos, sig_ep2-np.mean(sig_ep2[:10]))
    all_ProcData[i, :] = sig_fil

NameError: name 'pi' is not defined

In [ ]:
fig, ax1 = plt.subplots(figsize=(16,12))
t_begin = 162.5
t_end = 172.5

for i in arange (0,100,10):
    ax1.plot(t[int(t_begin*fs):int(t_end*fs)]-t[int(t_begin*fs)], all_ProcData[i, int(t_begin*fs):int(t_end*fs)])


ax1.set_ylabel('strain ($n\epsilon$)')

ax1.set_title('Traces during hammer shot - ping = 10 kHz, GL= 7m')

ax1.set_xlabel('Time (s)')



#### The variable 'all_ProcData' contains the processed (BP filtered) data as a matrix with the dimensions [time samples, channels] channels are every 1m along the fiber and the sample rate is 2.5 kHz.